In [1]:
# 配置迅投研数据服务
from vnpy.trader.setting import SETTINGS

SETTINGS["datafeed.name"] = "xt"
SETTINGS["datafeed.username"] = "token"
SETTINGS["datafeed.password"] = "4aff6f3b0dcfc990ec9476213ba784e17c34e757"

In [8]:
# 加载功能模块
from datetime import datetime

from xtquant.xtdata import (
    download_history_data,
    get_stock_list_in_sector,
    get_instrument_detail,
    get_option_detail_data
)

from vnpy.trader.datafeed import get_datafeed
from vnpy.trader.object import ContractData, Exchange, Product, OptionType

from elite_database import EliteDatabase

In [9]:
# 初始化数据服务
datafeed = get_datafeed()
datafeed.init()

True

In [10]:
# from xtquant import xtdata
get_stock_list_in_sector("过期上期所")

['ag1209.SF',
 'ag1210.SF',
 'ag1211.SF',
 'ag1212.SF',
 'ag1301.SF',
 'ag1302.SF',
 'ag1303.SF',
 'ag1304.SF',
 'ag1305.SF',
 'ag1306.SF',
 'ag1307.SF',
 'ag1308.SF',
 'ag1309.SF',
 'ag1310.SF',
 'ag1311.SF',
 'ag1312.SF',
 'ag1401.SF',
 'ag1402.SF',
 'ag1403.SF',
 'ag1404.SF',
 'ag1405.SF',
 'ag1406.SF',
 'ag1407.SF',
 'ag1408.SF',
 'ag1409.SF',
 'ag1410.SF',
 'ag1411.SF',
 'ag1412.SF',
 'ag1501.SF',
 'ag1502.SF',
 'ag1503.SF',
 'ag1504.SF',
 'ag1505.SF',
 'ag1506.SF',
 'ag1507.SF',
 'ag1508.SF',
 'ag1509.SF',
 'ag1510.SF',
 'ag1511.SF',
 'ag1512.SF',
 'ag1601.SF',
 'ag1602.SF',
 'ag1603.SF',
 'ag1604.SF',
 'ag1605.SF',
 'ag1606.SF',
 'ag1607.SF',
 'ag1608.SF',
 'ag1609.SF',
 'ag1610.SF',
 'ag1611.SF',
 'ag1612.SF',
 'ag1701.SF',
 'ag1702.SF',
 'ag1703.SF',
 'ag1704.SF',
 'ag1705.SF',
 'ag1706.SF',
 'ag1707.SF',
 'ag1708.SF',
 'ag1709.SF',
 'ag1710.SF',
 'ag1711.SF',
 'ag1712.SF',
 'ag1801.SF',
 'ag1802.SF',
 'ag1803.SF',
 'ag1804.SF',
 'ag1805.SF',
 'ag1806.SF',
 'ag1807.SF',
 'ag18

In [16]:
print(get_option_detail_data('ag2303C4750.SF'))

{}


In [ ]:
xtdata.download_history_data('CF111C20400.ZF',period = "1m")

In [ ]:
day_data = xtdata.get_market_data_ex([], ['CF111C20400.ZF'], period='1m', start_time='20000101', end_time='20231026', count=-1, dividend_type='front', fill_data=True)

In [ ]:
print(day_data)

In [ ]:
# 交易所映射关系
EXCHANGE_XT2VT = {
    "SH": Exchange.SSE,
    "SZ": Exchange.SZSE,
    "BJ": Exchange.BSE,
    "SF": Exchange.SHFE,
    "IF": Exchange.CFFEX,
    "INE": Exchange.INE,
    "DF": Exchange.DCE,
    "ZF": Exchange.CZCE,
    "GF": Exchange.GFEX
}


In [ ]:
# 下载历史合约信息
download_history_data("", "historycontract")

In [ ]:
# 查询中金所历史合约代码
cffex_symbols: list[str] = get_stock_list_in_sector("过期郑商所")
cffex_symbols[-60:-51]

In [ ]:
from xtquant import xtdata
xtdata.get_option_detail_data('ZC404P860.ZF')

In [ ]:
# 遍历列表查询合约信息
contracts: list[ContractData] = []

for xt_symbol in cffex_symbols:
    # 拆分XT代码
    symbol, xt_exchange = xt_symbol.split(".")

    # 筛选期权合约合约
    if "-" in symbol:
        data: dict = get_instrument_detail(xt_symbol, True)

        type_str = data["InstrumentID"].split("-")[1]
        if type_str == "C":
            option_type = OptionType.CALL
        elif type_str == "P":
            option_type = OptionType.PUT

        contract: ContractData = ContractData(
            symbol=data["InstrumentID"],
            exchange=EXCHANGE_XT2VT[xt_exchange.replace("O", "")],
            name=data["InstrumentName"],
            product=Product.OPTION,
            size=data["VolumeMultiple"],
            pricetick=data["PriceTick"],
            min_volume=data["MinLimitOrderVolume"],
            option_strike=data["ExtendInfo"]["OptExercisePrice"],
            option_listed=datetime.strptime(data["OpenDate"], "%Y%m%d"),
            option_expiry=datetime.strptime(data["ExpireDate"], "%Y%m%d"),
            option_portfolio=data["ProductID"],
            option_index=str(data["ExtendInfo"]["OptExercisePrice"]),
            option_type=option_type,
            gateway_name="XT"
        )
        contracts.append(contract)

print("数据长度", len(contracts))

In [ ]:
# 查看期权合约信息
contracts[0]

In [ ]:
# 创建Elite数据库实例
database: EliteDatabase = EliteDatabase()

In [ ]:
# 写入合约信息
database.save_contract_data(contracts)

In [ ]:
# 读取合约信息（全量）
loaded_contracts = database.load_contract_data()

In [ ]:
# 查看读取的合约信息
print(loaded_contracts[0])
print(loaded_contracts[-1])